In [122]:
import chardet
from BeautifulSoup import BeautifulSoup 
import re
import os
from nltk.stem.porter import PorterStemmer
from langdetect import detect
import pymorphy2
import regex
import pickle
import codecs
import docx
import numpy as np
import pandas as pd
from collections import defaultdict
from gensim import corpora, models, similarities
import operator
from gensim.summarization.bm25 import BM25

In [123]:
def detect_lang(str):
    return detect(str)

In [124]:
detect_lang("rfr cyznm jnntrb gjl ukfpfvb")

u'no'

In [130]:
Porter = PorterStemmer()
RusLem = pymorphy2.MorphAnalyzer()
UkLem = pymorphy2.MorphAnalyzer(lang='uk')

#разбиваем текст (unicode) на токены, приводим к нижнему регистру и применяем нормализацию
def TextParse(text):
    tokens = re.findall('[\w]+', text.lower(), re.U)
    #теперь стемминг зависит от языка. Надо его определить.
    if detect(text) == u'ru':        
        tokens = [RusLem.parse(token)[0].normal_form for token in tokens]
    elif detect(text) == u'uk':
        tokens = [UkLem.parse(token)[0].normal_form for token in tokens]
    elif detect(text) == u'en':
        tokens = [Porter.stem(token) for token in tokens]
    return tokens

def create_URL_IDX_dict(url_index_file):
    url_idx = {}
    f = open(url_index_file, "r")
    for line in f:
        l = line.strip().split()
        url_idx[l[1]] = l[0]
    return url_idx

def check_file(file_name):
    with open("./data_tokens" + file_name, 'rb') as res_file:
        tokens = pickle.load(res_file)
    print len(tokens)
    for t in tokens:
        print t
        
def create_idx_query_dict(idx_query_file):
    #по индексу выдает запрос, причем обработанный
    idx_query = {}
    f = open(idx_query_file, "r")
    for line in f:
        l = line.decode("utf-8").strip().split()
        idx_query[int(l[0])] = TextParse(" ".join(l[1:]))
    return idx_query

def create_IDX_URL_dict(url_index_file):
    idx_url = {}
    f = open(url_index_file, "r")
    for line in f:
        l = line.strip().split()
        idx_url[int(l[0])] = l[1]
    return idx_url

def get_doc_place():
    doc_place = {}
    for dir_name in os.listdir("./data_tokens_test/"):
        for file_name in os.listdir("./data_tokens_test/" + dir_name):
            doc_place[int(file_name)] = "./data_tokens_test/" + dir_name + "/" + file_name
            
    return doc_place

def get_part(docs_to_ranking, doc_place):
    part_dict = {}
    for q in docs_to_ranking.keys():
        sum_ = 0
        for doc in docs_to_ranking[q]:
            if doc in doc_place:
                sum_ += 1
        part_dict[q] = sum_/float(len(docs_to_ranking[q]))
    
    sorted_ = sorted(part_dict.items(), key=operator.itemgetter(1))
    return sorted_
        
def get_ready_doc_for_query(query_num, docs_to_ranking, doc_place):
    ready_doc = []
    for doc in docs_to_ranking[query_num]:
        if doc in doc_place:
            ready_doc.append(doc_place[doc])
    
    return ready_doc

def get_all_ready_doc(doc_place):
    ready_doc = []
    for doc in doc_place:
        ready_doc.append(doc_place[doc])
    return ready_doc

def check_file(file_name):
    with open(file_name, 'rb') as res_file:
        tokens = pickle.load(res_file)
    print len(tokens)
    for t in tokens:
        print t
        
def get_tokens_from_file(file_name):
    with open(file_name, 'rb') as res_file:
        tokens = pickle.load(res_file)
    return tokens

2017-03-24 20:18:51,654 : INFO : Loading dictionaries from /home/dana_zl/anaconda2/lib/python2.7/site-packages/pymorphy2_dicts_ru/data
2017-03-24 20:18:51,729 : INFO : format: 2.4, revision: 403871, updated: 2017-02-05T20:55:05.731216
2017-03-24 20:18:51,734 : INFO : Loading dictionaries from /home/dana_zl/anaconda2/lib/python2.7/site-packages/pymorphy2_dicts_uk/data
2017-03-24 20:18:51,784 : INFO : format: 2.4, revision: 1, updated: 2016-04-10T11:08:15.982658


In [131]:
URL_IDX = create_URL_IDX_dict("./urls.numerate.txt")
IDX_URL = create_IDX_URL_dict("./urls.numerate.txt")
IDX_QUERY = create_idx_query_dict("./queries.numerate_test.txt")

In [132]:
for t in IDX_QUERY[200]:
    print t
print IDX_URL[14361]

какой
гласный
ударный
и
безударный
http://mreporter.ru/reports/?page=13&tag=F.P.G


In [133]:
sample_submit = pd.read_csv("sample.csv").values
#номер запроса - список документов для ранжирования
docs_to_ranking = {}
for q in sample_submit:
#     print q
    if q[0] not in docs_to_ranking:
        docs_to_ranking[q[0]] = [q[1]]
    else:
        docs_to_ranking[q[0]].append(q[1])

In [134]:
print type(docs_to_ranking[1][0])

<type 'numpy.int64'>


In [135]:
print pd.read_csv("sample.csv")

       QueryId  DocumentId
0            1         222
1            1         244
2            1         842
3            1         851
4            1        1226
5            1        1229
6            1        1748
7            1        2699
8            1        3189
9            1        3667
10           1        4142
11           1        4845
12           1        4824
13           1        5539
14           1        6162
15           1        6293
16           1        8642
17           1        8785
18           1        9190
19           1        9443
20           1        9637
21           1        9943
22           1       10072
23           1       10100
24           1       10106
25           1       10112
26           1       10144
27           1       10149
28           1       10150
29           1       10152
...        ...         ...
27221      339       20306
27222      339       20349
27223      339       20551
27224      339       20700
27225      339       20840
2

In [136]:
doc_place = get_doc_place()
print len(doc_place)

26710


In [137]:
sorted_ = get_part(docs_to_ranking, doc_place)
print sorted_

[(36, 0.9418604651162791), (211, 0.9558823529411765), (240, 0.9583333333333334), (200, 0.963855421686747), (109, 0.9659090909090909), (149, 0.968421052631579), (7, 0.9746835443037974), (328, 0.975), (186, 0.9753086419753086), (194, 0.9764705882352941), (315, 0.9764705882352941), (60, 0.9767441860465116), (329, 0.9767441860465116), (224, 0.98), (92, 0.9807692307692307), (335, 0.984375), (142, 0.9852941176470589), (47, 0.9855072463768116), (27, 0.9857142857142858), (6, 0.9859154929577465), (129, 0.9864864864864865), (320, 0.9864864864864865), (71, 0.9868421052631579), (78, 0.9871794871794872), (170, 0.9871794871794872), (217, 0.9873417721518988), (23, 0.9875), (122, 0.9875), (123, 0.9875), (57, 0.9876543209876543), (331, 0.9876543209876543), (11, 0.9878048780487805), (48, 0.9878048780487805), (136, 0.9878048780487805), (228, 0.9878048780487805), (285, 0.9878048780487805), (155, 0.9879518072289156), (183, 0.9879518072289156), (225, 0.9879518072289156), (302, 0.9879518072289156), (310, 0.9

In [138]:
exp_doc = get_ready_doc_for_query(42, docs_to_ranking, doc_place)
for s in exp_doc:
    print IDX_URL[int(s.split("/")[-1])]
print len(docs_to_ranking[42])
for t in IDX_QUERY[42]:
    print t

http://anekdot.ru/an/an3304/o330422;18.html
http://anekdot.ru/an/an3308/o330823;12.html
http://anekdot.ru/search/?ch%5Bv%5D=on&page=1&query=%D0%B2%D0%BE%D0%B2%D0%BE%D1%87%D0%BA%D0%B0%20%D0%BF%D1%80%D0%B8%D0%B2%D0%B5%D0%BB%20%D0%B4%D0%BE%D0%BC%D0%BE%D0%B9%20%D0%BD%D0%B5%D0%BE%D0%BF%D1%8B%D1%82%D0%BD%D1%83%D1%8E%20%D0%BE%D0%B4%D0%BD%D0%BE%D0%BA%D0%BB%D0%B0%D1%81%D1%81%D0%BD%D0%B8%D1%86%D1%83&xcnt=100
http://anekdot.yoops.ru/anekdots/1/?page=2
http://ateism.ru/forum/index.php?topic=12537.0
http://berezovskii.ru/index.php?go=Anekdots&page=10
http://bibo.kz/anekdoti/vovochka/1064278-prihodit-vovochka-v-shkolu-s-opuhshey-guboy-ego-odnoklassniki-sprashiv.html
http://blogs.privet.ru/user/kuzyel?year=2007
http://bmw5erclub.ru/forum/archive/index.php/t-3097-p-5.html
http://bookz.ru/authors/sbornik/500-zolo_639/1-500-zolo_639.html
http://caliberclub.ru/forum/archive/index.php/t-68-p-14.html
http://club-yeti.ru/forum/archive/index.php/t-177-p-15.html
http://copypast.ru/2009/08/14/anekdoty_pro_vovo

In [139]:
check_file("./data_tokens_test/2/16428")

956
if
lt
ie
8
body
class
no
js
lt
ie10
lt
ie9
lt
ie8
endif
if
ie
8
body
class
no
js
lt
ie10
lt
ie9
ie8
endif
if
ie
9
body
class
no
js
lt
ie10
ie
9
endif
if
gt
ie
9
endif
1872
tns
counter
ru
tns
counter
ru
1872
счётчик
для
рейтинг
4243
4243
плашка
с
версия
браузер
3355
noindex
mail
ru
почта
мой
мир
одноклассник
игра
знакомство
новость
поиск
весь
проект
весь
проект
выход
регистрация
вход
if
ie
7
script
var
____________ie7
true
script
endif
if
ie
8
script
var
____________ie8
true
script
endif
noindex
3355
категория
весь
вопрос
проект
компьютер
интернет
тема
для
взрослый
авто
мото
красота
и
здоровье
товар
и
услуга
бизнес
финансы
наука
техника
язык
философия
непознанный
город
и
страна
образование
фотография
видеосъемка
гороскоп
магия
гадание
общество
политика
сми
юридический
консультация
досуг
развлечение
путешествие
туризм
юмор
еда
кулинария
работа
карьера
о
проект
mail
ru
животное
растение
семья
дом
ребёнок
другой
знакомство
любовь
отношение
спорт
золотой
фонд
искусство
и
культура
стиль


In [140]:
ready_docs = get_all_ready_doc(doc_place)
print len(ready_docs)

26710


In [141]:
def bprint(l):
    for x in l:
        print x
    print
    
    
#для каждого ранжируемого документа составим список новых токенов, состоящих из 2 слов
def get_2_grams_tokens_from_file(file_name):
    with open(file_name, 'rb') as res_file:
        tokens = pickle.load(res_file)
#     bprint(tokens[:15])
    tokens_2 = []
    for ind, token in enumerate(tokens[:-1]):
        tokens_2.append(token + " " + tokens[ind + 1])
    
    return tokens_2

def get_3_grams_tokens_from_file(file_name):
    with open(file_name, 'rb') as res_file:
        tokens = pickle.load(res_file)
        
    tokens_3 = []
    for ind, token in enumerate(tokens[:-2]):
        tokens_3.append(token + " " + tokens[ind + 1] + " " + tokens[ind + 2])
    
    return tokens_3

#создаем 3 списка всех пар слов: слова из подряд, слова идут в обратном порядке, слова через один
def get_2_grams_from_query(query):
    pair_forward = []
    pair_inverse = []
    pair_through_one = []
    
    for ind, q in enumerate(query[:-1]):
        pair_forward.append(q + " " + query[ind + 1])
        if ind < (len(query) - 2):
            pair_through_one.append(q + " " + query[ind + 2])
    
    for ind, q in enumerate(query[1:]):
        #ind на один меньше настоящего из-за enumerate
        pair_inverse.append(q + " " + query[ind])
        
    return pair_forward, pair_inverse, pair_through_one


#создаем списка всех подряд идющих слов
def get_3_grams_from_query(query):
    triple_forward = []
    
    for ind, q in enumerate(query[:-2]):
        triple_forward.append(q + " " + query[ind + 1] + " " +  query[ind + 2])
        
    return triple_forward

def create_tokens_list_for_query(num_query, docs_to_ranking, doc_place, tokens_type = 1):
    docs_for_corpus = get_ready_doc_for_query(num_query, docs_to_ranking, doc_place)

    docs_tokens=[]
    num_documents=0

    for doc_name in docs_for_corpus:
        if tokens_type == 1:
            docs_tokens.append(get_tokens_from_file(doc_name))
        if tokens_type == 2:
            docs_tokens.append(get_2_grams_tokens_from_file(doc_name))
        if tokens_type == 3:
            docs_tokens.append(get_3_grams_tokens_from_file(doc_name))
        num_documents+=1
    
    print "Count of Documents: ", num_documents
    return docs_tokens, num_documents, docs_for_corpus

In [142]:
def create_corpus(docs_tokens, dict_file_name, corpora_file_name):
    dictionary = corpora.Dictionary(docs_tokens)

    # store the dictionary, to file for future reference (I love python's handling of files!)
    dictionary.save(dict_file_name)

    # Verify what is in there!
    print "Count docs in Dictionary:", dictionary.num_docs

    # This is the main object. the corpus
    corpus = [dictionary.doc2bow(tokens) for tokens in docs_tokens]

    # store to disk, for later use
    corpora.MmCorpus.serialize(corpora_file_name, corpus)
    
    return dictionary, corpus

In [7]:
docs_tokens, _, docs_for_corpus = create_tokens_list_for_query(1, docs_to_ranking, doc_place, tokens_type = 1)
dictionary, corpus = create_corpus(docs_tokens, dict_file_name="./test_dict", corpora_file_name="./test_corpora")


new_doc = IDX_QUERY[1]
for t in new_doc:
    print t
new_vec = dictionary.doc2bow(new_doc)
 
# both words have been found and this is the resulting vector...
print new_vec
 
# Let's play with tfidf, we transform corpus...
tfidf = models.TfidfModel(corpus)

NameError: name 'docs_to_ranking' is not defined

In [37]:
dictionary.doc2bow(get_tokens_from_file("./data_tokens_test/2/16428"))

[(2, 2),
 (11, 1),
 (18, 1),
 (20, 6),
 (27, 1),
 (32, 6),
 (38, 23),
 (42, 5),
 (44, 3),
 (46, 10),
 (52, 1),
 (57, 1),
 (63, 1),
 (64, 3),
 (66, 10),
 (69, 12),
 (75, 3),
 (79, 7),
 (82, 5),
 (88, 1),
 (92, 6),
 (99, 3),
 (100, 1),
 (104, 1),
 (129, 1),
 (133, 1),
 (141, 3),
 (146, 1),
 (147, 1),
 (160, 2),
 (161, 9),
 (163, 1),
 (164, 1),
 (166, 1),
 (168, 2),
 (176, 3),
 (187, 5),
 (189, 1),
 (197, 1),
 (200, 11),
 (201, 1),
 (208, 1),
 (218, 1),
 (219, 1),
 (221, 1),
 (224, 5),
 (225, 1),
 (231, 2),
 (242, 1),
 (257, 2),
 (261, 1),
 (262, 1),
 (263, 4),
 (266, 3),
 (268, 8),
 (278, 2),
 (284, 1),
 (290, 2),
 (294, 3),
 (300, 17),
 (302, 5),
 (309, 1),
 (312, 1),
 (313, 1),
 (321, 1),
 (325, 1),
 (327, 1),
 (334, 2),
 (337, 2),
 (338, 4),
 (591, 1),
 (598, 1),
 (599, 1),
 (613, 1),
 (619, 1),
 (628, 1),
 (632, 1),
 (637, 1),
 (639, 5),
 (655, 1),
 (660, 1),
 (664, 3),
 (681, 3),
 (682, 1),
 (707, 1),
 (712, 2),
 (714, 1),
 (717, 1),
 (719, 1),
 (725, 1),
 (758, 1),
 (760, 1),
 (767

In [38]:
# building up the index...
index = similarities.Similarity('./tmp', tfidf[corpus], num_features=len(dictionary))

# save the index for later use
index.save('./first_index')

In [39]:
vec_tfidf=tfidf[new_vec]
sims = index[vec_tfidf]
sims = sorted(enumerate(sims), key=lambda item: -item[1])
for s in sims:
    print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]

(0, 0.0) ./data_tokens_test/20/222 http://36on.ru/forum/topics/show/133
(1, 0.0) ./data_tokens_test/96/244 http://3koketki.ru/meshki-pod-glazami-sredstva-dlya-ustraneniya.html
(2, 0.0) ./data_tokens_test/20/842 http://all2lady.ru/kak-snyat-oteki-s-glaz
(3, 0.0) ./data_tokens_test/50/851 http://alla-i-k.ru/article/careforperson/oedema_eyelid
(4, 0.0) ./data_tokens_test/14/1226 http://arabio.ru/sovety/oteki_pod_glazami.htm
(5, 0.0) ./data_tokens_test/81/1229 http://arabio.ru/zdo/otek_lica.htm
(6, 0.0) ./data_tokens_test/49/1748 http://ayzdorov.ru/lechenie_otek_pod_glazami.php
(7, 0.0) ./data_tokens_test/1/2699 http://bodyskin.ru/kak-snyat-oteki-s-glaz
(8, 0.0) ./data_tokens_test/82/3189 http://caringmother.ru/634-kak-ubrat-oteki-pod-glazami-v-domashnih-usloviyah-ekspress-metody-luchshee-sredstvo-i-krem-ot-otekov-pod-glazami.html
(9, 0.0) ./data_tokens_test/77/3667 http://colady.ru/16-dejstvennyx-receptov-snyat-oteki-pod-glazami.html
(10, 0.0) ./data_tokens_test/26/4142 http://dama.info/k

In [40]:
bprint(docs_tokens[54])

if
lt
ie
body
class
no
js
lt
ie
lt
ie
lt
ie
endif
if
ie
body
class
no
js
lt
ie
lt
ie
ie
endif
if
ie
body
class
no
js
lt
ie
ie
endif
mail
ru
почта
мой
мир
одноклассник
игра
знакомство
новость
поиск
весь
проект
весь
проект
выход
регистрация
вход
категория
весь
вопрос
проект
компьютер
интернет
тема
для
взрослый
авто
мото
красота
и
здоровье
товар
и
услуга
бизнес
финансы
наука
техника
язык
философия
непознанный
город
и
страна
образование
фотография
видеосъемка
гороскоп
магия
гадание
общество
политика
сми
юридический
консультация
досуг
развлечение
путешествие
туризм
юмор
еда
кулинария
работа
карьера
о
проект
mail
ru
животное
растение
семья
дом
ребёнок
другой
знакомство
любовь
отношение
спорт
золотой
фонд
искусство
и
культура
стиль
мода
звезда
полный
список
спросить
лидер
поиск
по
вопрос
ответ
mail
ru
красота
и
здоровье
баня
массаж
фитнес
болезнь
лекарство
врач
клиника
страхование
детский
здоровье
здоровый
образ
жизнь
коррекция
вес
косметика
парфюмерия
маникюр
педикюр
салон
красота
и
спа
уход

In [41]:
a, b, c = get_2_grams_from_query(IDX_QUERY[331])
bprint(IDX_QUERY[331])
bprint(a)
bprint(b)
bprint(c)

что
такой
волевой
человек

что такой
такой волевой
волевой человек

такой что
волевой такой
человек волевой

что волевой
такой человек



In [43]:
docs_tokens, _, docs_for_corpus = create_tokens_list_for_query(331, docs_to_ranking, doc_place, tokens_type = 2)
dictionary, corpus = create_corpus(docs_tokens, dict_file_name="./test_dict", corpora_file_name="./test_corpora")

Count of Documents:  79
Count docs in Dictionary: 79


In [44]:
bprint(docs_tokens[0])

хороший форум
форум меню
меню навигация
навигация форум
форум участник
участник правило
правило поиск
поиск регистрация
регистрация галерея
галерея форум
форум летопись
летопись best
best fm
fm войти
войти пользовательский
пользовательский ссылка
ссылка активный
активный тема
тема информация
информация о
о пользователь
пользователь привет
привет гость
гость войти
войти или
или зарегистрироваться
зарегистрироваться вы
вы здесь
здесь хороший
хороший форум
форум здоровье
здоровье что
что такой
такой сон
сон и
и как
как он
он хороший
хороший использовать
использовать что
что такой
такой сон
сон и
и как
как он
он хороший
хороший использовать
использовать страница
страница сообщение
сообщение страница
страница из
из поделиться
поделиться автор
автор nbsp
nbsp svetik
svetik администратор
администратор откуда
откуда саратов
саратов сообщение
сообщение уважение
уважение позитив
позитив последний
последний визит
визит личный
личный счёт
счёт в
в награда
награда подарок
подарок разведать
разведат

In [46]:
# building up the index...
index = similarities.Similarity('./tmp', tfidf[corpus], num_features=len(dictionary))

# save the index for later use
index.save('./first_index')

In [47]:
vec_tfidf=tfidf[vec_forward]
sims = index[vec_tfidf]
sims = sorted(enumerate(sims), key=lambda item: -item[1])
for s in sims:
    print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]

(48, 0.10676388) ./data_tokens_test/9/18294 http://psyera.ru/2513/volevoy-chelovek
(30, 0.01569894) ./data_tokens_test/71/13425 http://megaobuchalka.ru/6/35493.html
(68, 0.012555978) ./data_tokens_test/74/22036 http://studfiles.ru/preview/3284165/page:11
(15, 0.0093735149) ./data_tokens_test/65/9225 http://infourok.ru/chto_takoe_volevye_sposobnosti_cheloveka-134006.htm
(70, 0.0036136522) ./data_tokens_test/90/22558 http://svet-unlimited.ucoz.ru/forum/75-1038-2
(44, 0.00051079015) ./data_tokens_test/87/17286 http://pochit.ru/istoriya/22188/index.html
(54, 0.00038857816) ./data_tokens_test/85/18870 http://referat7.ru/refs/source/ref666-102420.html
(66, 0.00028326362) ./data_tokens_test/16/21168 http://slovorus.ru/index.php?ID=87422&a&pg=65&s=%C2&w=%C2%CE%CB%C5%C2%CE%C9
(50, 0.00026452102) ./data_tokens_test/22/18953 http://referat.ru/referat/chto-takoe-cvoe-delo-622309/2
(71, 0.00024724301) ./data_tokens_test/93/22713 http://tampereclub.ru/961-chto-takoe-lyubovnaya-zavisimost.html
(43, 0

In [48]:
for c in "dsdg":
    print c

d
s
d
g


In [143]:
letters_dict = {'q':u'й', 'w':u'ц', 'e':u'у', 'r':u'к', 't':u'е', 'y':u'н', \
                'u':u'г', 'i':u'ш', 'o':u'щ', 'p':u'з', '[':u'х', ']':u'ъ', \
                'a':u'ф', 's':u'ы', 'd':u'в', 'f':u'а', 'g':u'п', 'h':u'р', \
                'j':u'о', 'k':u'л', 'l':u'д', ';':u'ж', '\'':u'э', 'z':u'я', \
                'x':u'ч', 'c':u'с', 'v':u'м', 'b':u'и', 'n':u'т', 'm':u'ь',\
                ',':u'б', '.':u'ю', '`':u'ё', '?':u',', u' ':u' ', u'е':u'e', \
                u'й':u'й', u'ц':u'ц', u'у':u'у', u'к':u'к', u'н':u'н', u'г':u'г', \
                u'ш':u'ш', u'щ':u'щ', u'з':u'з', u'х':u'х', u'ъ':u'ъ', u'ф':u'ф', \
                u'ы':u'ы', u'в':u'в', u'а':u'а', u'п':u'п', u'р':u'р', u'о':u'о', \
                u'л':u'л', u'д':u'д', u'ж':u'ж', u'э':u'э', u'я':u'я', u'ч':u'ч', \
                u'с':u'с', u'м':u'м', u'и':u'и', u'т':u'т', u'ь':u'ь', u'б':u'б', \
                u'ю':u'ю',  u'ё':u'ё', u'\u0456':u'\u0456'}

def inverse_letters(tokens):
    new_tokens = []
    for token in tokens:
        new_token = "".join([letters_dict[c] for c in token])
        new_tokens.append(new_token)
    
    return new_tokens

In [144]:
#order_type - если выбираем токены из двух слов, обозначает порядок слов: forward, inverse or through_one ???
#если tokens_type = 2 - выбираем токены, по 2 слова в каждом, возвращаем матрицу sims - 
#для токенов запроса в прямом, обратном и порядке через одно слово.
def simple_TF_IDF_for_query(query_num, inverse = False, tokens_type = 1):
    docs_tokens, _, docs_for_corpus = create_tokens_list_for_query(query_num, docs_to_ranking, doc_place, \
                                                                   tokens_type = tokens_type)
    
    dictionary, corpus = create_corpus(docs_tokens, dict_file_name="./simple_dict", \
                                       corpora_file_name="./simple_corpora")
    
    query_tokens = IDX_QUERY[query_num]
    
    if tokens_type == 1:
        query_tokens_stop = [token for token in IDX_QUERY[query_num]  if token not in stop_words]
        if len(query_tokens) > 0:
            query_tokens = query_tokens_stop
    
    if tokens_type == 2:
        q_forward, q_inverse, q_through_one = get_2_grams_from_query(query_tokens)
#         query_tokens = q_forward+ q_inverse + q_through_one
        query_tokens = q_forward
    
    if tokens_type == 3:
        q_forward = get_3_grams_from_query(query_tokens)
#         query_tokens = q_forward+ q_inverse + q_through_one
        query_tokens = q_forward
        
    if inverse:
        query_tokens = inverse_letters(query_tokens)
        
    query_vec = dictionary.doc2bow(query_tokens)
    
    print "Query number,", query_num
    bprint(query_tokens)
#     print query_vec

    tfidf = models.TfidfModel(corpus)
    # building up the index...
    index = similarities.Similarity('./tmp', tfidf[corpus], num_features=len(dictionary))

    # save the index for later use
#     index.save('./simple_index')
    vec_tfidf=tfidf[query_vec]
#     print query_vec
    
    sims = index[vec_tfidf]
    sims = sorted(enumerate(sims), key=lambda item: -item[1])
    
    return sims, docs_for_corpus

#создаю словарь: номер документа - score
def create_dict_from_sims(sims, docs_for_corpus):
    res = {}
    for s in sims:
        res[ int(docs_for_corpus[s[0]].split("/")[-1])] = s[1]
    return res

In [146]:
#{запрос:{документ:вес}}
W_single = {}
#делаем сабмит простого TF-IDF
for ind, query_num in enumerate(docs_to_ranking.keys()):
    sims, docs_for_corpus = simple_TF_IDF_for_query(query_num)
    #проверка на то, что вообще хоть что-то нашлось - возможно стоит попробовать инвертировать запрос
    if sims and sims[0][1] != 0.0:
        W_single[query_num] = create_dict_from_sims(sims, docs_for_corpus)
        for s in sims[:10]:
            print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]
            
    else:
        sims, docs_for_corpus = simple_TF_IDF_for_query(query_num, inverse = True)
        for s in sims[:10]:
            print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]
        W_single[query_num] = create_dict_from_sims(sims, docs_for_corpus)

2017-03-24 20:20:13,176 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2017-03-24 20:20:13,319 : INFO : built Dictionary(10106 unique tokens: [u'\u043f\u0440\u043e\u0434\u0435\u0444\u0438\u043b\u0438\u0440\u043e\u0432\u0430\u0442\u044c', u'\u0440\u0430\u0441\u0442\u0435\u043d\u0438\u0435', u'\u043f\u043e\u043e\u0447\u0435\u0440\u0451\u0434\u043d\u044b\u0439', u'\u0441\u0443\u0442\u043a\u0438', u'\u0434\u0440\u0435\u043d\u0430\u0436']...) from 89 documents (total 125667 corpus positions)
2017-03-24 20:20:13,320 : INFO : saving Dictionary object under ./simple_dict, separately None
2017-03-24 20:20:13,347 : INFO : saved ./simple_dict


Count of Documents:  89
Count docs in Dictionary: 89


2017-03-24 20:20:13,481 : INFO : storing corpus in Matrix Market format to ./simple_corpora
2017-03-24 20:20:13,482 : INFO : saving sparse matrix to ./simple_corpora
2017-03-24 20:20:13,483 : INFO : PROGRESS: saving document #0
2017-03-24 20:20:13,688 : INFO : saved 89x10106 matrix, density=5.259% (47300/899434)
2017-03-24 20:20:13,689 : INFO : saving MmCorpus index to ./simple_corpora.index
2017-03-24 20:20:13,690 : INFO : collecting document frequencies
2017-03-24 20:20:13,693 : INFO : PROGRESS: processing document #0
2017-03-24 20:20:13,706 : INFO : calculating IDF weights for 89 documents and 10105 features (47300 matrix non-zeros)
2017-03-24 20:20:13,714 : INFO : starting similarity index under ./tmp
2017-03-24 20:20:13,813 : INFO : creating sparse index
2017-03-24 20:20:13,814 : INFO : creating sparse matrix from corpus
2017-03-24 20:20:13,816 : INFO : PROGRESS: at document #0/89


Query number, 1
rfr
cyznm
jntrb
gjl
ukfpfvb



2017-03-24 20:20:13,903 : INFO : created <89x10106 sparse matrix of type '<type 'numpy.float32'>'
	with 47300 stored elements in Compressed Sparse Row format>
2017-03-24 20:20:13,904 : INFO : creating sparse shard #0
2017-03-24 20:20:13,905 : INFO : saving index shard to ./tmp.0
2017-03-24 20:20:13,905 : INFO : saving SparseMatrixSimilarity object under ./tmp.0, separately None
2017-03-24 20:20:13,907 : INFO : saved ./tmp.0
2017-03-24 20:20:13,908 : INFO : loading SparseMatrixSimilarity object from ./tmp.0
2017-03-24 20:20:13,909 : INFO : loaded ./tmp.0
2017-03-24 20:20:14,414 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2017-03-24 20:20:14,564 : INFO : built Dictionary(10106 unique tokens: [u'\u043f\u0440\u043e\u0434\u0435\u0444\u0438\u043b\u0438\u0440\u043e\u0432\u0430\u0442\u044c', u'\u0440\u0430\u0441\u0442\u0435\u043d\u0438\u0435', u'\u043f\u043e\u043e\u0447\u0435\u0440\u0451\u0434\u043d\u044b\u0439', u'\u0441\u0443\u0442\u043a\u0438', u'\u0434\u0440\u0435\u043d\

...

(76, 0.31144831) ./data_tokens_test/70/25802 http://yakpros.ru/nauka/46377-shho-take-soda.html
(66, 0.29420704) ./data_tokens_test/23/23046 http://tips-ua.com/152213-shho-take-soda.html
(38, 0.22199467) ./data_tokens_test/38/14602 http://myhelper.com.ua/index.php?newsid=14919
(59, 0.14125778) ./data_tokens_test/86/21160 http://slovopedia.org.ua/29/53409/20915.html
(67, 0.06173436) ./data_tokens_test/12/23526 http://tvoetilo.com.ua/yak_shudnuty_za_dopomogoiu_sody.php
(80, 0.029777067) ./data_tokens_test/54/25929 http://ykrnews.com/zdorove/chomu-sodova-d-ta-nebezpechna.html
(13, 0.028449474) ./data_tokens_test/66/6243 http://faqukr.ru/izha-ta-napoi/89349-shho-take-sodova-i-jak-ii-prigotuvati.html
(6, 0.02648963) ./data_tokens_test/99/3193 http://carpatia.if.ua/shho-take-sodova-3
(20, 0.020241581) ./data_tokens_test/79/7904 http://gbud.com.ua/jak-miti-mikrohvilovku
(32, 0.018088536) ./data_tokens_test/61/12970 http://mamslady.ru/kulinarija/3736-oladki-na-moloci-5-smachnih-receptiv.html


2017-03-24 20:59:17,978 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2017-03-24 20:59:18,084 : INFO : built Dictionary(14335 unique tokens: [u'\u043f\u0435\u0434\u043e\u0444\u0438\u0442\u0438', u'\u0430\u0443\u0434\u0438\u0442\u043e\u0440\u0456\u044f', u'\u0440\u0430\u0441\u0442\u0435\u043d\u0438\u0435', u'\u0433\u043e\u0442\u043e\u0432\u0456', u'\u043d\u0432\u0440']...) from 87 documents (total 73310 corpus positions)
2017-03-24 20:59:18,085 : INFO : saving Dictionary object under ./simple_dict, separately None
2017-03-24 20:59:18,114 : INFO : saved ./simple_dict


Count of Documents:  87
Count docs in Dictionary: 87


2017-03-24 20:59:18,206 : INFO : storing corpus in Matrix Market format to ./simple_corpora
2017-03-24 20:59:18,207 : INFO : saving sparse matrix to ./simple_corpora
2017-03-24 20:59:18,208 : INFO : PROGRESS: saving document #0
2017-03-24 20:59:18,356 : INFO : saved 87x14335 matrix, density=2.819% (35162/1247145)
2017-03-24 20:59:18,357 : INFO : saving MmCorpus index to ./simple_corpora.index
2017-03-24 20:59:18,358 : INFO : collecting document frequencies
2017-03-24 20:59:18,359 : INFO : PROGRESS: processing document #0
2017-03-24 20:59:18,371 : INFO : calculating IDF weights for 87 documents and 14334 features (35162 matrix non-zeros)
2017-03-24 20:59:18,384 : INFO : starting similarity index under ./tmp
2017-03-24 20:59:18,464 : INFO : creating sparse index
2017-03-24 20:59:18,465 : INFO : creating sparse matrix from corpus
2017-03-24 20:59:18,466 : INFO : PROGRESS: at document #0/87
2017-03-24 20:59:18,526 : INFO : created <87x14335 sparse matrix of type '<type 'numpy.float32'>'
	w

Query number, 339
що
такий
чванливість

(73, 0.025415972) ./data_tokens_test/69/24248 http://verano.rv.ua/navkolishnij-svit/shho-take-sonce
(1, 0.02163671) ./data_tokens_test/45/420 http://5ka.at.ua/load/tvori/shho_take_shhastja_1_variant_tvir/59-1-0-16673
(56, 0.020397993) ./data_tokens_test/68/19517 http://rss.novostimira.com/n_5290030.html
(42, 0.018118998) ./data_tokens_test/29/14238 http://mosaic.if.ua/shho-take-riznicja-3
(63, 0.018025029) ./data_tokens_test/17/21676 http://sseo.pp.ua/shho-take-domen
(32, 0.016301746) ./data_tokens_test/88/11500 http://leton.org/persona/persona/scho-take-depresiya-i-yak-z-neyu-borotisya.html
(80, 0.01473526) ./data_tokens_test/61/25484 http://women.in.ua/scho-take-povnotsinnyj-shlyub.html
(36, 0.013171215) ./data_tokens_test/55/13139 http://matrasnazakaz.org.ua/?p=90022
(0, 0.013069226) ./data_tokens_test/40/32 http://1000ask.info/entsyklopediia/vsesvit/56-shcho-take-asteroid
(58, 0.01288058) ./data_tokens_test/89/20349 http://sankiev.com.ua/shho

In [78]:
with open("./W_single_new", 'wb') as res_file:
    pickle.dump(W_single, res_file)

In [19]:
with open("./W_single_new", 'rb') as res_file:
    W_single = pickle.load(res_file)

In [79]:
print W_single[10]

{24577: 0.0, 14859: 0.0063439487, 24592: 0.010816144, 10773: 0.0035420433, 2582: 0.0, 10776: 0.14031827, 10785: 0.17809293, 10280: 0.0016547216, 10797: 0.17293628, 13363: 0.04745663, 7733: 0.00044777925, 12343: 0.0080158878, 19637: 0.0033415938, 10818: 0.046841696, 19523: 0.0076699094, 7245: 0.026832011, 17080: 0.14498968, 12370: 0.0089510586, 13918: 0.025560919, 9829: 0.07221254, 7271: 0.012133151, 26732: 0.078450836, 21104: 0.0, 26738: 0.047217451, 22643: 0.0, 5236: 0.0047431882, 26746: 0.03324987, 14459: 0.19251521, 3199: 0.020510584, 6787: 0.020329304, 6678: 0.025875559, 3207: 0.059817106, 14988: 0.01078149, 3215: 0.17123973, 6288: 0.076180808, 3218: 0.0014175056, 4755: 0.020198625, 1176: 0.0, 25774: 0.018842984, 18609: 0.0016147573, 9907: 0.0, 5301: 0.0065344186, 25784: 0.081056744, 24768: 0.056930311, 19139: 0.004915162, 14534: 0.023875246, 14543: 0.022030046, 26321: 0.0, 21210: 0.0097959852, 25825: 0.038155526, 24300: 0.051357657, 24301: 0.01730928, 24302: 0.074883148, 4853: 0.0

In [80]:
W_pair = {}
for ind, query_num in enumerate(docs_to_ranking.keys()):
    sims_2, docs_for_corpus = simple_TF_IDF_for_query(query_num, tokens_type=2)
    #проверка на то, что вообще хоть что-то нашлось - возможно стоит попробовать инвертировать запрос
    if sims_2 and sims_2[0][1] != 0.0:
        W_pair[query_num] = create_dict_from_sims(sims_2, docs_for_corpus)
        for s in sims_2[:10]:
            print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]
            
    else:
        sims_2, docs_for_corpus = simple_TF_IDF_for_query(query_num, inverse = True, tokens_type=2)
        if sims_2 and sims_2[0][1] == 0.0: 
            W_pair[query_num] = None
            continue
        for s in sims_2[:10]:
            print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]
        
        W_pair[query_num] = create_dict_from_sims(sims_2,docs_for_corpus)

Count of Documents:  89
Count docs in Dictionary: 89
Query number, 1
rfr cyznm
cyznm jntrb
jntrb gjl
gjl ukfpfvb

Count of Documents:  89
Count docs in Dictionary: 89
Query number, 1
как снять
снять отеки
отеки под
под глазами

(65, 0.045768604) ./data_tokens_test/19/20597 http://sdelayu-sama.ru/index.php/krasota/kak-snyat-oteki-s-glaz.html
(24, 0.042930026) ./data_tokens_test/94/10106 http://kakprosto.ru/kak-36018-kak-snyat-otyoki-i-sinyaki
(27, 0.033344045) ./data_tokens_test/59/10149 http://kakprosto.ru/kak-8397-kak-snyat-otek-glaz
(28, 0.032919053) ./data_tokens_test/94/10150 http://kakprosto.ru/kak-83984-kak-snyat-otek-s-glaza-ot-udara
(58, 0.028398182) ./data_tokens_test/97/16555 http://otvet.mail.ru/question/70260658
(21, 0.027586296) ./data_tokens_test/33/9943 http://justlady.ru/articles-149460-kak-snyat-silnye-oteki
(62, 0.026544984) ./data_tokens_test/17/17174 http://pinme.ru/u/kondrat/kak-snyat-oteki-pod-glazami
(23, 0.025312081) ./data_tokens_test/6/10100 http://kakprosto.r

In [81]:
with open("./W_pair_new", 'wb') as res_file:
    pickle.dump(W_pair, res_file)

In [83]:
with open("./W_pair_new", 'rb') as res_file:
    W_pair = pickle.load(res_file)

In [149]:
W_triple = {}
for ind, query_num in enumerate(docs_to_ranking.keys()):
    sims_2, docs_for_corpus = simple_TF_IDF_for_query(query_num, tokens_type=3)
    #проверка на то, что вообще хоть что-то нашлось - возможно стоит попробовать инвертировать запрос
    if sims_2 and sims_2[0][1] != 0.0:
        W_triple[query_num] = create_dict_from_sims(sims_2, docs_for_corpus)
        for s in sims_2[:10]:
            print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]
            
    else:
        try:
            sims_2, docs_for_corpus = simple_TF_IDF_for_query(query_num, inverse = True, tokens_type=3)
        except Exception as ex:
            print ex
        if sims_2 and sims_2[0][1] == 0.0: 
            W_triple[query_num] = None
            continue
        for s in sims_2[:10]:
            print s, docs_for_corpus[s[0]], IDX_URL[int(docs_for_corpus[s[0]].split("/")[-1])]
        
        W_triple[query_num] = create_dict_from_sims(sims_2,docs_for_corpus)

2017-03-24 21:39:40,129 : INFO : adding document #0 to Dictionary(0 unique tokens: [])


Count of Documents:  89


2017-03-24 21:39:40,486 : INFO : built Dictionary(80901 unique tokens: [u'\u043c\u043e\u0436\u043d\u043e \u0434\u0435\u043b\u0430\u0442\u044c \u0440\u0430\u0437\u043d\u044b\u0439', u'\u043a\u0430\u0440\u0434\u0438\u043d\u0430\u043b\u044c\u043d\u043e \u0440\u0430\u0441\u0445\u043e\u0434\u0438\u0442\u044c\u0441\u044f \u043f\u0440\u0438\u043c\u043e\u0447\u043a\u0430', u'\u0441\u0438\u044f\u0442\u044c \u0441\u043e\u0432\u0435\u0442 \u043a\u0440\u043e\u043c\u0435', u'\u043d\u0435\u0431\u044b\u0442\u044c \u043d\u043e \u043f\u043e\u0442\u043e\u043c', u'sbquo \xf0\xb2\xf0 \xf1']...) from 89 documents (total 125489 corpus positions)
2017-03-24 21:39:40,487 : INFO : saving Dictionary object under ./simple_dict, separately None
2017-03-24 21:39:40,589 : INFO : saved ./simple_dict
2017-03-24 21:39:40,733 : INFO : storing corpus in Matrix Market format to ./simple_corpora
2017-03-24 21:39:40,734 : INFO : saving sparse matrix to ./simple_corpora
2017-03-24 21:39:40,736 : INFO : PROGRESS: saving docu

Count docs in Dictionary: 89


2017-03-24 21:39:41,162 : INFO : saved 89x80901 matrix, density=1.417% (102027/7200189)
2017-03-24 21:39:41,163 : INFO : saving MmCorpus index to ./simple_corpora.index
2017-03-24 21:39:41,164 : INFO : collecting document frequencies
2017-03-24 21:39:41,165 : INFO : PROGRESS: processing document #0
2017-03-24 21:39:41,204 : INFO : calculating IDF weights for 89 documents and 80900 features (102027 matrix non-zeros)
2017-03-24 21:39:41,275 : INFO : starting similarity index under ./tmp


...

2017-03-24 23:37:53,468 : INFO : saved ./simple_dict
2017-03-24 23:37:53,559 : INFO : storing corpus in Matrix Market format to ./simple_corpora
2017-03-24 23:37:53,560 : INFO : saving sparse matrix to ./simple_corpora
2017-03-24 23:37:53,561 : INFO : PROGRESS: saving document #0


Count docs in Dictionary: 87


2017-03-24 23:37:53,822 : INFO : saved 87x62345 matrix, density=1.201% (65162/5424015)
2017-03-24 23:37:53,823 : INFO : saving MmCorpus index to ./simple_corpora.index
2017-03-24 23:37:53,824 : INFO : collecting document frequencies
2017-03-24 23:37:53,825 : INFO : PROGRESS: processing document #0
2017-03-24 23:37:53,854 : INFO : calculating IDF weights for 87 documents and 62344 features (65162 matrix non-zeros)
2017-03-24 23:37:53,902 : INFO : starting similarity index under ./tmp
2017-03-24 23:37:54,012 : INFO : creating sparse index
2017-03-24 23:37:54,012 : INFO : creating sparse matrix from corpus
2017-03-24 23:37:54,014 : INFO : PROGRESS: at document #0/87


Query number, 339
що такий чванливість



2017-03-24 23:37:54,122 : INFO : created <87x62345 sparse matrix of type '<type 'numpy.float32'>'
	with 65162 stored elements in Compressed Sparse Row format>
2017-03-24 23:37:54,123 : INFO : creating sparse shard #0
2017-03-24 23:37:54,123 : INFO : saving index shard to ./tmp.0
2017-03-24 23:37:54,124 : INFO : saving SparseMatrixSimilarity object under ./tmp.0, separately None
2017-03-24 23:37:54,125 : INFO : saved ./tmp.0
2017-03-24 23:37:54,126 : INFO : loading SparseMatrixSimilarity object from ./tmp.0
2017-03-24 23:37:54,127 : INFO : loaded ./tmp.0


In [49]:
with open("./W_triple", 'wb') as res_file:
    pickle.dump(W_triple, res_file)

In [220]:
print u'\u0456'

і


In [113]:
print W_single[40]
print len(W_single[4])
print W_pair[40]
print len(W_single[4])

{2953: 0.0002502343, 5281: 6.1617808e-05, 10370: 0.00072040933, 16337: 0.0, 4356: 0.0, 10373: 0.013991191, 21513: 0.0066024689, 525: 0.0046667452, 21646: 0.0002489592, 6036: 0.0010655541, 7959: 0.0028575761, 7192: 0.0073617483, 8644: 0.0045015994, 11930: 0.0010083622, 4763: 0.062253255, 5532: 0.043982767, 11317: 0.0010059064, 5278: 0.011533032, 5279: 0.00010879828, 11632: 0.00042144809, 11196: 0.00018213534, 23195: 0.0, 23716: 0.00081340183, 23599: 0.0, 6183: 0.019702863, 2354: 0.0036510793, 5277: 7.2343704e-05, 2353: 0.00089931895, 11570: 0.0082880734, 1203: 0.0010970221, 15668: 0.0032894558, 9269: 0.0089876205, 13449: 0.0015501502, 5956: 0.0012905232, 9785: 0.0063128504, 1951: 0.0, 14396: 0.0023814677, 6077: 0.0, 7614: 0.005806379, 1855: 0.010751001, 23873: 0.0, 20583: 0.0016476077, 17348: 0.0045895297, 13509: 0.013122512, 25414: 0.0025972102, 25415: 0.013320013, 11977: 0.00039444811, 587: 0.0082253721, 5453: 0.036212929, 10958: 0.00096043508, 4303: 0.0, 23377: 0.0026584852, 9908: 0.

In [84]:
def create_ensemble(query_dict_list, coef_list):
    res_ranks = {}
    for query_num in query_dict_list[0].keys():
        res_rank = {}
        for doc in query_dict_list[0][query_num].keys():
            res_rank[doc] = 0
            for ind, rank in enumerate(query_dict_list):
                if rank[query_num]:
#                     print query_num
                    res_rank[doc] += rank[query_num][doc] * coef_list[ind]
        res_ranks[query_num] = res_rank
    return res_ranks

In [147]:
res = create_ensemble([W_single, W_pair], [1, 1.0])
for query_num in res.keys():
    res[query_num] = sorted(res[query_num].items(), key=operator.itemgetter(1), reverse=True)[:10]

for query_num in res.keys():
    print query_num
    bprint(IDX_QUERY[query_num])
    for doc in res[query_num]:
#         print doc[0],  doc[1]
        if W_pair[query_num]:
            print doc[0],  doc[1], W_single[query_num][doc[0]],  W_pair[query_num][doc[0]], IDX_URL[doc[0]]
        else:
            print doc[0],  doc[1], W_single[query_num][doc[0]],  "None", IDX_URL[doc[0]]

simple_submit = []
for query_num in res.keys():
    bprint(IDX_QUERY[query_num])
    for ind, doc in enumerate(res[query_num]):
        simple_submit.append([query_num, doc[0]])
#         print doc[0],  doc[1], IDX_URL[doc[0]]
# np.savetxt("single_pair_1_new.csv", simple_submit, "%i", delimiter=",", header='QueryId,DocumentId')

1
rfr
cyznm
jntrb
gjl
ukfpfvb

10106 0.0811888948083 0.0382589 0.04293 http://kakprosto.ru/kak-36018-kak-snyat-otyoki-i-sinyaki
20597 0.0756825041026 0.0299139 0.0457686 http://sdelayu-sama.ru/index.php/krasota/kak-snyat-oteki-s-glaz.html
10149 0.0664380379021 0.033094 0.033344 http://kakprosto.ru/kak-8397-kak-snyat-otek-glaz
10072 0.0607545543462 0.0441024 0.0166522 http://kakprosto.ru/kak-120106-kak-bystro-snyat-otek-glaz
10150 0.0557685345411 0.0228495 0.0329191 http://kakprosto.ru/kak-83984-kak-snyat-otek-s-glaza-ot-udara
17174 0.0523838996887 0.0258389 0.026545 http://pinme.ru/u/kondrat/kak-snyat-oteki-pod-glazami
25333 0.0514408610761 0.0278573 0.0235836 http://womanadvice.ru/kak-snyat-oteki-s-glaz
10153 0.0502075273544 0.0287449 0.0214626 http://kakprosto.ru/kak-84961-kak-snyat-oteki-i-sinyaki-s-glaz
10100 0.0480452682823 0.0227332 0.0253121 http://kakprosto.ru/kak-28237-kak-snyat-otyok-gorla
14790 0.0447145011276 0.0213325 0.023382 http://naomi.ru/services/plastic/blefaroplasty

In [148]:
save_res(res, "./new_single_pair_digit.csv")

In [44]:
print_res(res)

rfr
cyznm
jntrb
gjl
ukfpfvb

1
10106 0.0833451263607 http://kakprosto.ru/kak-36018-kak-snyat-otyoki-i-sinyaki
20597 0.0778410434723 http://sdelayu-sama.ru/index.php/krasota/kak-snyat-oteki-s-glaz.html
10149 0.0685639679432 http://kakprosto.ru/kak-8397-kak-snyat-otek-glaz
10072 0.0634002946317 http://kakprosto.ru/kak-120106-kak-bystro-snyat-otek-glaz
10150 0.0571435876191 http://kakprosto.ru/kak-83984-kak-snyat-otek-s-glaza-ot-udara
17174 0.0536616556346 http://pinme.ru/u/kondrat/kak-snyat-oteki-pod-glazami
25333 0.0531727932394 http://womanadvice.ru/kak-snyat-oteki-s-glaz
10153 0.0518942829221 http://kakprosto.ru/kak-84961-kak-snyat-oteki-i-sinyaki-s-glaz
10100 0.0495692659169 http://kakprosto.ru/kak-28237-kak-snyat-otyok-gorla
4824 0.0493894014508 http://domashniemaski.ru/kak-snyat-otek-lica.html
банк
выставить
счёт
за
плата
за
использование
кредит
сверх
лимит
законно
ли
это

2
9912 0.0836818814278 http://jurdiskus.ru/kak_propisatj_summu_v_dogovore.html
6836 0.0833208411932 http://for

In [120]:
#считаю W_all_words = k1 * tfidf * k2**n_miss
#для этого понадобится только query_sims

W_all_words = {}
for ind, query_num in enumerate(docs_to_ranking.keys()):
    len_query = len(IDX_QUERY[query_num])
    query_tokens = [token for token in IDX_QUERY[query_num]  if token not in stop_words]
    bprint(query_tokens)
    print query_num
    docs_tokens, _, docs_for_corpus = create_tokens_list_for_query(query_num, docs_to_ranking, doc_place, \
                                                                   tokens_type = 1)
    
    W_all_words[query_num] = {}
    docs_for_corpus = [int(docs_for_corpus[s].split("/")[-1]) for s in range(len(docs_for_corpus))]
    need_inverse = 1
    for ind, doc in enumerate(docs_for_corpus):
        not_in_doc = sum([1 for token in query_tokens  if token not in docs_tokens[ind] ])
        if not_in_doc < len(query_tokens):
            need_inverse = 0
        W_all_words[query_num][doc] =  W_single[query_num][doc] * 0.6**not_in_doc
#         print doc, IDX_URL[doc], W_all_words[query_num][doc] 

    if need_inverse == 1:
        query_tokens = inverse_letters(query_tokens)
        print query_tokens
        
        for ind, doc in enumerate(docs_for_corpus):
            not_in_doc = sum([1 for token in query_tokens  if token not in docs_tokens[ind] ])
            W_all_words[query_num][doc] = W_single[query_num][doc] * 0.6**not_in_doc
#             print doc, IDX_URL[doc], not_in_doc

rfr
cyznm
jntrb
gjl
ukfpfvb

1
Count of Documents:  89
[u'\u043a\u0430\u043a', u'\u0441\u043d\u044f\u0442\u044c', u'\u043e\u0442\u0435\u043a\u0438', u'\u043f\u043e\u0434', u'\u0433\u043b\u0430\u0437\u0430\u043c\u0438']
банк
выставить
счёт
плата
использование
кредит
сверх
лимит
законно

2
Count of Documents:  82
срок
год
сбор
зимний
яблоко
волгоград

3
Count of Documents:  81
проект
занятый
дмитрий
шепелевый

4
Count of Documents:  87
возраст
стерилизовать
кошка

5
Count of Documents:  84
полушарие
находиться
россия

6
Count of Documents:  70
заключаться
работа
администратор
офис

7
Count of Documents:  77
различие
ос
андроид
5
1
андроид
6
0

8
Count of Documents:  82
видеть

9
Count of Documents:  81
сколько
месяц
брать
котёнок
кошка

10
Count of Documents:  86
вбить
дать
доверенный
лицо
получать
денежный
средство
пко
1с

11
Count of Documents:  81
гай
стоять
ижевск

12
Count of Documents:  90
давать
земля
многодетный
усманский
район

13
Count of Documents:  72
делать
компьютерный
томо

In [90]:
with open("./W_all_words_new", 'wb') as res_file:
    pickle.dump(W_all_words, res_file)

In [56]:
W_all_words[200]

{1257: 0.0052152425050735474,
 1378: 0.026464641094207764,
 2146: 0.014725612476468086,
 2229: 0.021789746358990669,
 2643: 0.029607821255922318,
 2693: 0.00027130239084362983,
 2809: 0.028271183371543884,
 2814: 0.028434708714485168,
 3675: 2.9749510483816266e-05,
 4122: 0.00042124653831124303,
 4626: 0.034884978085756302,
 5093: 0.015246251598000526,
 5187: 0.066368594765663147,
 5718: 0.0,
 5860: 0.023318329825997353,
 6041: 0.048886939883232117,
 6167: 0.048435255885124207,
 6340: 0.045698255300521851,
 6510: 0.0,
 7910: 0.0,
 8740: 0.0091512970626354221,
 9094: 0.0,
 9320: 0.088809266686439514,
 9403: 0.0092328675091266632,
 9987: 0.0010206671655178068,
 10190: 0.10221178829669952,
 10353: 0.00047626636661589144,
 10609: 0.047252580523490906,
 10765: 0.023395221680402756,
 11194: 0.033367335796356201,
 11504: 0.043115328997373581,
 11619: 0.025158368051052094,
 11679: 0.030663924291729927,
 11680: 0.06560342013835907,
 11685: 0.070130378007888794,
 11758: 0.06685137003660202,
 117

In [150]:
res = create_ensemble([W_single, W_pair, W_triple], [1, 1.0, 1.0, 1.0])
for query_num in res.keys():
    res[query_num] = sorted(res[query_num].items(), key=operator.itemgetter(1), reverse=True)[:10]

for query_num in res.keys():
    bprint(IDX_QUERY[query_num])
    print query_num
    for doc in res[query_num]:
        if  W_pair[query_num] and W_triple[query_num]:
            print doc[0], W_single[query_num][doc[0]],  W_triple[query_num][doc[0]], \
                        W_pair[query_num][doc[0]], IDX_URL[doc[0]]
        elif  W_pair[query_num]:
            print doc[0], W_single[query_num][doc[0]],"None", \
                        W_pair[query_num][doc[0]],  IDX_URL[doc[0]]
        elif W_triple[query_num]:
            print doc[0], W_single[query_num][doc[0]], \
                         W_triple[query_num][doc[0]], "None", IDX_URL[doc[0]]
        

# simple_submit = []
# for query_num in res.keys():
#     bprint(IDX_QUERY[query_num])
#     for ind, doc in enumerate(res[query_num]):
#         simple_submit.append([query_num, doc[0]])
#         print doc[0],  doc[1], IDX_URL[doc[0]]
# np.savetxt("single_pair_all_new.csv", simple_submit, "%i", delimiter=",", header='QueryId,DocumentId')

rfr
cyznm
jntrb
gjl
ukfpfvb

1
10106 0.0382589 None 0.04293 http://kakprosto.ru/kak-36018-kak-snyat-otyoki-i-sinyaki
20597 0.0299139 None 0.0457686 http://sdelayu-sama.ru/index.php/krasota/kak-snyat-oteki-s-glaz.html
10149 0.033094 None 0.033344 http://kakprosto.ru/kak-8397-kak-snyat-otek-glaz
10072 0.0441024 None 0.0166522 http://kakprosto.ru/kak-120106-kak-bystro-snyat-otek-glaz
10150 0.0228495 None 0.0329191 http://kakprosto.ru/kak-83984-kak-snyat-otek-s-glaza-ot-udara
17174 0.0258389 None 0.026545 http://pinme.ru/u/kondrat/kak-snyat-oteki-pod-glazami
25333 0.0278573 None 0.0235836 http://womanadvice.ru/kak-snyat-oteki-s-glaz
10153 0.0287449 None 0.0214626 http://kakprosto.ru/kak-84961-kak-snyat-oteki-i-sinyaki-s-glaz
10100 0.0227332 None 0.0253121 http://kakprosto.ru/kak-28237-kak-snyat-otyok-gorla
14790 0.0213325 None 0.023382 http://naomi.ru/services/plastic/blefaroplasty/oteki-glaz
банк
выставить
счёт
за
плата
за
использование
кредит
сверх
лимит
законно
ли
это

2
6836 0.0550553 

In [151]:
save_res(res, "./single_pair_triple.csv")

In [153]:
def tf_query_in_doc(query_tokens, doc_tokens):
    cnt_tokens = len(query_tokens)
    query_text = ' '.join(query_tokens)
    tf = 0
    for ind in range(len(doc_tokens) - cnt_tokens + 1):
#         print ' '.join(doc_tokens[ind:(cnt_tokens + ind)])
        if query_text == ' '.join(doc_tokens[ind:(cnt_tokens + ind)]):
            tf += 1
    return tf

In [154]:
tf_query_in_doc(["тро","ло","ло"], ["тро", "ло", "ло","лошара", "тро", "ло", "ло"])

2

In [155]:
#W_phrase - бонус для вхождения всего запроса в документ
W_phrase = {}
for ind, query_num in enumerate(docs_to_ranking.keys()):
    query_tokens = IDX_QUERY[query_num]
    if query_num == 1:
        query_tokens = inverse_letters(query_tokens)
    bprint(query_tokens)
    print query_num
    docs_tokens, _, docs_for_corpus = create_tokens_list_for_query(query_num, docs_to_ranking, doc_place, \
                                                                   tokens_type = 1)
    
    W_phrase[query_num] = {}
    docs_for_corpus = [int(docs_for_corpus[s].split("/")[-1]) for s in range(len(docs_for_corpus))]
    for ind, doc in enumerate(docs_for_corpus):
        
        query_tf = tf_query_in_doc(query_tokens, docs_tokens[ind])
        if query_tf != 0:
            print "!=0!"
        W_phrase[query_num][doc] = W_single[query_num][doc] * query_tf / float((query_tf + 1))
#         print doc, IDX_URL[doc], not_in_doc

как
снять
отеки
под
глазами

1
Count of Documents:  89
банк
выставить
счёт
за
плата
за
использование
кредит
сверх
лимит
законно
ли
это

2
Count of Documents:  82
в
какой
срок
в
это
год
сбор
зимний
яблоко
в
волгоград

3
Count of Documents:  81
в
какой
проект
занятый
дмитрий
шепелевый

4
Count of Documents:  87
в
какой
возраст
стерилизовать
кошка

5
Count of Documents:  84
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
в
какой
полушарие
находиться
россия

6
Count of Documents:  70
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
в
чем
заключаться
работа
администратор
офис

7
Count of Documents:  77
в
чем
различие
между
ос
андроид
5
1
и
андроид
6
0

8
Count of Documents:  82
видеть
ли
вы

9
Count of Documents:  81
!=0!
!=0!
!=0!
!=0!
!=0!
!=0!
в
сколько
месяц
можно
брать
котёнок
от
кошка

10
Count of Documents:  86
где
вбить
дать
доверенный
лицо
получать
денежный
средство
через
пко
в
1с

11
Count of Documents:  81
где
га

In [156]:
print W_phrase[9]

{17024: 0.0, 19606: 0.0, 21122: 0.0, 15619: 0.0, 13189: 0.0, 21102: 0.0, 1159: 0.0, 12535: 0.0, 18364: 0.0, 2442: 0.0, 907: 0.0, 3981: 0.0, 22030: 0.0, 2064: 0.034941919147968292, 23569: 0.0, 14866: 0.0, 21396: 0.0, 8725: 0.0, 790: 0.0, 15895: 0.0, 5272: 0.0, 6170: 0.0, 5531: 0.0, 23749: 0.0, 14371: 0.0, 7462: 0.0, 988: 0.0, 4906: 0.0, 20395: 0.0, 22551: 0.0, 16429: 0.0039037636015564203, 21901: 0.0, 24620: 0.0, 7218: 0.0075315488502383232, 9203: 0.0, 24471: 0.0, 23945: 0.0, 2616: 0.0, 7737: 0.0, 24762: 0.0, 19643: 0.0, 15036: 0.0, 11325: 0.0, 7743: 0.0, 5312: 0.0, 22653: 0.0, 18499: 0.0, 10052: 0.0, 23621: 0.0030321313533931971, 24033: 0.0, 8190: 0.0, 5323: 0.0, 333: 0.0056420746259391308, 2765: 0.016081912443041801, 1872: 0.0, 20536: 0.0, 9556: 0.0, 26638: 0.0, 16953: 0.0, 6233: 0.0, 3164: 0.0, 21084: 0.0, 11024: 0.0, 14614: 0.0, 26339: 0.0, 18148: 0.0, 7397: 0.0, 24593: 0.0, 16232: 0.0, 4457: 0.0, 20462: 0.0, 4335: 0.0, 3827: 0.0, 7285: 0.0, 5225: 0.0, 2424: 0.0, 25876: 0.0, 7935: 0

In [160]:
res = create_ensemble([W_single, W_pair, W_triple, W_phrase], [1, 1, 1, 1.5])
for query_num in res.keys():
    res[query_num] = sorted(res[query_num].items(), key=operator.itemgetter(1), reverse=True)[:10]

for query_num in res.keys():
    bprint(IDX_QUERY[query_num])
    print query_num
    for doc in res[query_num]:
#         if W_pair[query_num] and W_triple[q]:
        print doc[0], W_phrase[query_num][doc[0]], IDX_URL[doc[0]]
#         else:
#             print doc[0], W_single[query_num][doc[0]],"None", \
#                         W_all_words[query_num][doc[0]], W_phrase[query_num][doc[0]], IDX_URL[doc[0]]
        

simple_submit = []
for query_num in res.keys():
#     bprint(IDX_QUERY[query_num])
    for ind, doc in enumerate(res[query_num]):
        simple_submit.append([query_num, doc[0]])
#         print doc[0],  doc[1], IDX_URL[doc[0]]
# np.savetxt("single_pair_phrase.csv", simple_submit, "%i", delimiter=",", header='QueryId,DocumentId')

rfr
cyznm
jntrb
gjl
ukfpfvb

1
10106 0.0 http://kakprosto.ru/kak-36018-kak-snyat-otyoki-i-sinyaki
20597 0.0 http://sdelayu-sama.ru/index.php/krasota/kak-snyat-oteki-s-glaz.html
10149 0.0 http://kakprosto.ru/kak-8397-kak-snyat-otek-glaz
10072 0.0 http://kakprosto.ru/kak-120106-kak-bystro-snyat-otek-glaz
10150 0.0 http://kakprosto.ru/kak-83984-kak-snyat-otek-s-glaza-ot-udara
17174 0.0 http://pinme.ru/u/kondrat/kak-snyat-oteki-pod-glazami
25333 0.0 http://womanadvice.ru/kak-snyat-oteki-s-glaz
10153 0.0 http://kakprosto.ru/kak-84961-kak-snyat-oteki-i-sinyaki-s-glaz
10100 0.0 http://kakprosto.ru/kak-28237-kak-snyat-otyok-gorla
14790 0.0 http://naomi.ru/services/plastic/blefaroplasty/oteki-glaz
банк
выставить
счёт
за
плата
за
использование
кредит
сверх
лимит
законно
ли
это

2
6836 0.0 http://forum.anti-rs.ru/topic/11671-%D1%83%D0%BC%D0%B5%D0%BD%D1%8C%D1%88%D0%B5%D0%BD%D0%B8%D0%B5-%D0%BB%D0%B8%D0%BC%D0%B8%D1%82%D0%B0-%D0%BA%D0%B0%D1%80%D1%82%D1%8B-%D0%B8%D0%B7-%D0%B7%D0%B0-%D0%BF%D1%80%D0%BE%

In [161]:
save_res(res, "./single_pair_triple_phrase.csv")

In [152]:
def print_diff(res_1, res_2, type_2 = None):
    for query_num in res_1.keys():
#         print type(res_2[query_num])
        for ind in range(10):
            if (type_2 == 'submit' and res_1[query_num][ind][0] != res_2[query_num][ind]) or \
                        (type_2 != 'submit' and res_1[query_num][ind][0] != res_2[query_num][ind][0]):
                bprint(IDX_QUERY[query_num])
                print query_num, ind
                print "__________________1____________________"
                for doc in res_1[query_num]:
                    print doc[0],  doc[1], IDX_URL[doc[0]]
                print "__________________2____________________"
                for doc in res_2[query_num]:
                    if type_2 == 'submit':
                        print doc,  IDX_URL[doc]
                    else:
                        print doc[0], IDX_URL[doc[0]]
                break
                
def print_res(res):
    for query_num in res.keys():
        bprint(IDX_QUERY[query_num])
        print query_num

        for doc in res[query_num]:
            print doc[0],  doc[1], IDX_URL[doc[0]]
            
def save_res(res, file_name):
    simple_submit = []
    for query_num in res.keys():
    #     bprint(IDX_QUERY[query_num])
        for ind, doc in enumerate(res[query_num]):
            simple_submit.append([query_num, doc[0]])
    #         print doc[0],  doc[1], IDX_URL[doc[0]]
    np.savetxt(file_name, simple_submit, "%i", delimiter=",", header='QueryId,DocumentId')

In [160]:
res_1 = create_ensemble([W_single, W_pair, W_all_words, W_phrase], [1, 1, 1, 1])
for query_num in res_1.keys():
    res_1[query_num] = sorted(res_1[query_num].items(), key=operator.itemgetter(1), reverse=True)[:10]
    
res_2 = create_ensemble([W_single, W_pair, W_phrase], [1, 1, 0.7])
for query_num in res_2.keys():
    res_2[query_num] = sorted(res_2[query_num].items(), key=operator.itemgetter(1), reverse=True)[:10]

print_diff(res_1, res_2)

банк
выставить
счёт
за
плата
за
использование
кредит
сверх
лимит
законно
ли
это

2 3
__________________1____________________
9912 0.114896375313 http://jurdiskus.ru/kak_propisatj_summu_v_dogovore.html
6836 0.0953880237788 http://forum.anti-rs.ru/topic/11671-%D1%83%D0%BC%D0%B5%D0%BD%D1%8C%D1%88%D0%B5%D0%BD%D0%B8%D0%B5-%D0%BB%D0%B8%D0%BC%D0%B8%D1%82%D0%B0-%D0%BA%D0%B0%D1%80%D1%82%D1%8B-%D0%B8%D0%B7-%D0%B7%D0%B0-%D0%BF%D1%80%D0%BE%D0%BF%D1%83%D1%81%D0%BA%D0%B0-%D0%BF%D0%BB%D0%B0%D1%82%D0%B5%D0%B6%D0%B5%D0%B9-%D0%B2-%D0%B4%D1%80%D1%83%D0%B3%D0%B8%D1%85-%D0%B1%D0%B0%D0%BD%D0%BA%D0%B0%D1%85/?page=2
26413 0.0713384778798 http://zakon-trm.ru/vzyskanie_na_imuschestvo_s_schet_dolga.html
1529 0.0570456270128 http://audit-it.ru/articles/account/buhaccounting/a6/44410.html
263 0.0496547877043 http://42.krg.msudrf.ru/modules.php?cl=1&id=1974&name=info_pages
6706 0.0450644406956 http://f-mx.ru/buxuchet_upravlenchuchet/buxgalteriya_predpriyatiya.html
25709 0.0371876199245 http://xn--90afdbaav0bd1afy6e

In [162]:
save_res(res_1, "./new_all_w.csv")

In [163]:
print_res(res_1)

rfr
cyznm
jnntrb
gjl
ukfpfvb

1
25333 0.0703592364345 http://womanadvice.ru/kak-snyat-oteki-s-glaz
10072 0.0490265248679 http://kakprosto.ru/kak-120106-kak-bystro-snyat-otek-glaz
10106 0.0459114951871 http://kakprosto.ru/kak-36018-kak-snyat-otyoki-i-sinyaki
10149 0.0394972931355 http://kakprosto.ru/kak-8397-kak-snyat-otek-glaz
20597 0.0377178029803 http://sdelayu-sama.ru/index.php/krasota/kak-snyat-oteki-s-glaz.html
10153 0.033226779958 http://kakprosto.ru/kak-84961-kak-snyat-oteki-i-sinyaki-s-glaz
4824 0.0320391518379 http://domashniemaski.ru/kak-snyat-otek-lica.html
11262 0.0307289429341 http://ladyspecial.ru/krasota/uxod-za-liczom-i-telom/kosmetologiya/kak-snyat-otek-s-glaz-posle-slez
17174 0.0305481111042 http://pinme.ru/u/kondrat/kak-snyat-oteki-pod-glazami
10150 0.0284086450376 http://kakprosto.ru/kak-83984-kak-snyat-otek-s-glaza-ot-udara
банк
выставить
счёт
за
плата
за
использование
кредит
сверх
лимит
законно
ли
это

2
9912 0.114896375313 http://jurdiskus.ru/kak_propisatj_summu_

In [137]:
old_res = {}
old_submit = pd.read_csv("./single_pair_phrase.csv").values
for q in old_submit:
#     print q
    if q[0] not in old_res:
        old_res[q[0]] = [q[1]]
    else:
        old_res[q[0]].append(q[1])

In [155]:
print old_res[1][0]

25333


In [159]:
print_diff(res_1, old_res, type_2='submit')

банк
выставить
счёт
за
плата
за
использование
кредит
сверх
лимит
законно
ли
это

2 5
__________________1____________________
9912 0.114896375313 http://jurdiskus.ru/kak_propisatj_summu_v_dogovore.html
6836 0.0953880237788 http://forum.anti-rs.ru/topic/11671-%D1%83%D0%BC%D0%B5%D0%BD%D1%8C%D1%88%D0%B5%D0%BD%D0%B8%D0%B5-%D0%BB%D0%B8%D0%BC%D0%B8%D1%82%D0%B0-%D0%BA%D0%B0%D1%80%D1%82%D1%8B-%D0%B8%D0%B7-%D0%B7%D0%B0-%D0%BF%D1%80%D0%BE%D0%BF%D1%83%D1%81%D0%BA%D0%B0-%D0%BF%D0%BB%D0%B0%D1%82%D0%B5%D0%B6%D0%B5%D0%B9-%D0%B2-%D0%B4%D1%80%D1%83%D0%B3%D0%B8%D1%85-%D0%B1%D0%B0%D0%BD%D0%BA%D0%B0%D1%85/?page=2
26413 0.0713384778798 http://zakon-trm.ru/vzyskanie_na_imuschestvo_s_schet_dolga.html
1529 0.0570456270128 http://audit-it.ru/articles/account/buhaccounting/a6/44410.html
263 0.0496547877043 http://42.krg.msudrf.ru/modules.php?cl=1&id=1974&name=info_pages
6706 0.0450644406956 http://f-mx.ru/buxuchet_upravlenchuchet/buxgalteriya_predpriyatiya.html
25709 0.0371876199245 http://xn--90afdbaav0bd1afy6e

In [114]:
from nltk.corpus import stopwords

stop_words = stopwords.words('russian')
stop_words.extend([u'что', u'это', u'так', u'вот', u'быть', u'как', u'в', u'—', u'к', u'на', u'такое'])

for s in stop_words:
    print s

и
в
во
не
что
он
на
я
с
со
как
а
то
все
она
так
его
но
да
ты
к
у
же
вы
за
бы
по
только
ее
мне
было
вот
от
меня
еще
нет
о
из
ему
теперь
когда
даже
ну
вдруг
ли
если
уже
или
ни
быть
был
него
до
вас
нибудь
опять
уж
вам
ведь
там
потом
себя
ничего
ей
может
они
тут
где
есть
надо
ней
для
мы
тебя
их
чем
была
сам
чтоб
без
будто
чего
раз
тоже
себе
под
будет
ж
тогда
кто
этот
того
потому
этого
какой
совсем
ним
здесь
этом
один
почти
мой
тем
чтобы
нее
сейчас
были
куда
зачем
всех
никогда
можно
при
наконец
два
об
другой
хоть
после
над
больше
тот
через
эти
нас
про
всего
них
какая
много
разве
три
эту
моя
впрочем
хорошо
свою
этой
перед
иногда
лучше
чуть
том
нельзя
такой
им
более
всегда
конечно
всю
между
что
это
так
вот
быть
как
в
—
к
на
такое


In [100]:
import nltk
nltk.download()

showing info https://raw.githubusercontent.com/nltk/nltk_data/gh-pages/index.xml


True